# Optimization of the dataset
The original dataset zise is about 3GB whitch is too much to use it without problem. This code will optmize the original dataset and save a smaller copy to use
Optimizations:
+ `reduce_columns` eliminate some dataset atrinutes that are not usefull for this analysis
+ `reduce_mem_usage` downcast int types to smaller types
+ `reduce_rows` 


In [3]:
# external dependencies
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

In [13]:
# constants file
from constants import *


### Population Dataset

In [6]:
# load dataset for US population
df_pop = pd.read_csv('US_Population.csv')
df_pop.dropna()
df_pop.head()


Year  Alabama  Alaska  Arizona  Arkansas  California  Colorado  \
0  2016  4860545  741522  6941072   2989918    39250017   5540545   
1  2017  4874747  739786  7044008   3001345    39536653   5607154   
2  2018  4887681  735139  7158024   3009733    39776830   5691287   
3  2019  4903185  731158  7278717   3017804    39576757   5758736   
4  2020  4921532  727890  7421401   3029887    39368078   5845526   

   Connecticut  Delaware   Florida  ...  South Dakota  Tennessee     Texas  \
0      3576452    952065  20612439  ...        865454    6651194  27862596   
1      3573880    961939  20928863  ...        869666    6715984  28304596   
2      3573297    971180  21244317  ...        878698    6771631  28704330   
3      3571520    981822  21538187  ...        882235    6829174  29145505   
4      3565287    990837  21899341  ...        886667    6886834  29618533   

      Utah  Vermont  Virginia  Washington  West Virginia  Wisconsin  Wyoming  
0  3051217   624594   8411808     7288000        1831102    5778708   585501  
1  3101833   623657   8470020     7423362        1818157    5790186   584910  
2  3153550   624344   8517685     7535591        1804291    5807406   578668  
3  3205958   624358   8565256     7614893        1792147    5822434   577601  
4  3251617   623989   8616207     7693612        1778070    5837466   567025  

[5 rows x 51 columns]

### Accident Dataset

In [7]:

# import dataset for US accident
df_acc = pd.read_csv('US_Accidents.csv')

# remove unecessary columns
df_acc.drop(['Source', 'Start_Lat', 'Start_Lng', 'End_Lat', 'End_Lng', 'Description', 'Airport_Code'], axis=1, inplace=True)

# remove null values
df_acc.dropna()

# sample a subset of the database (for efficency)
df_acc = df_acc.sample(n = 70000, random_state = 351)

# Convert 'Start_Time' and 'End_Time to datetime
df_acc['Start_Time'] = pd.to_datetime(df_acc['Start_Time'],format='ISO8601')
df_acc['End_Time'] = pd.to_datetime(df_acc['End_Time'],format='ISO8601')

# remove year 2023 because it is incomplete
df_acc = df_acc[(df_acc['Start_Time'].dt.year != 2023)]

df_acc.head()

ID  Severity          Start_Time            End_Time  \
2909380  A-2919259         3 2018-02-28 19:10:31 2018-02-28 19:55:17   
4123847  A-4154878         2 2022-11-22 16:09:03 2022-11-22 17:26:55   
7006131  A-7055452         2 2020-06-24 20:28:00 2020-06-24 21:02:05   
1191012  A-1200791         2 2021-01-08 18:01:03 2021-01-08 18:47:15   
453540    A-453553         2 2017-05-11 08:05:29 2017-05-11 08:34:56   

         Distance(mi)          Street         City            County State  \
2909380          0.00       Carson St     Lakewood       Los Angeles    CA   
4123847          0.99          I-40 W    Nashville          Davidson    TN   
7006131          0.00          I-94 E  Minneapolis          Hennepin    MN   
1191012          0.00    S Choctaw Dr  Baton Rouge  East Baton Rouge    LA   
453540           0.02  Meridian Ave N      Seattle              King    WA   

            Zipcode  ... Roundabout Station   Stop  Traffic_Calming  \
2909380       90715  ...      False   False  False            False   
4123847       37205  ...      False   False  False            False   
7006131       55412  ...      False   False  False            False   
1191012  70815-8901  ...      False   False  False            False   
453540   98133-8540  ...      False   False  False            False   

         Traffic_Signal  Turning_Loop  Sunrise_Sunset  Civil_Twilight  \
2909380           False         False           Night           Night   
4123847           False         False             Day             Day   
7006131           False         False             Day             Day   
1191012            True         False           Night           Night   
453540             True         False             Day             Day   

        Nautical_Twilight  Astronomical_Twilight  
2909380             Night                    Day  
4123847               Day                    Day  
7006131               Day                    Day  
1191012               Day                    Day  
453540                Day                    Day  

[5 rows x 39 columns]

### First graph (Single bar version):
Accident distribution (Year, Month, Day of the week, Hour)

In [8]:

def SingleBarChart(df, TimeInterval):

    if (TimeInterval == 'Yearly'):
        yearly_counts = df['Start_Time'].dt.year.value_counts().sort_index()
        fig = px.bar(
            x = yearly_counts.index, 
            y = yearly_counts.values,          
            labels = {'x': 'Year', 'y': 'Number of Accidents'},
            title = 'Number of Accidents per Year'
        )
        return fig
    
    if (TimeInterval == 'Monthly'):
        monthly_counts = df['Start_Time'].dt.month.value_counts().sort_index()
        fig = px.bar(
            x = monthly_counts.index, 
            y = monthly_counts.values,          
            labels = {'x': 'Month', 'y': 'Number of Accidents'},
            title = 'Number of Accidents per Month'
        )
        return fig
   
    if (TimeInterval == 'Daily'):
        daily_counts = df['Start_Time'].dt.dayofweek.value_counts().sort_index()
        day_names = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
        fig = px.bar(
            x = [day_names[day] for day in daily_counts.index], 
            y = daily_counts.values,          
            labels = {'x': 'Day of the Week', 'y': 'Number of Accidents'},
            title = 'Number of Accidents per Day'
        )
        return fig
    
    if (TimeInterval == 'Hourly'):
        hourly_counts = df['Start_Time'].dt.hour.value_counts().sort_index()
        fig = px.bar(
            x = hourly_counts.index, 
            y = hourly_counts.values,          
            labels = {'x': 'Hour', 'y': 'Number of Accidents'},
            title = 'Number of Accidents per Hour'
        )
        return fig


SingleBarChart(df_acc,'Monthly').show()

### First graph (Multi bar version):
Accident distribution (Year, Month, Day of the week, Hour)

In [9]:
def MultiBarChart(df, TimeInterval):
    #devide dataset on severity of the accident
    Severity1 = df[df.Severity == 1]
    Severity2 = df[df.Severity == 2]
    Severity3 = df[df.Severity == 3]
    Severity4 = df[df.Severity == 4]
    
    if (TimeInterval == 'Yearly'):
        categories = df['Start_Time'].dt.year.value_counts().sort_index().index

        values1 = Severity1['Start_Time'].dt.year.value_counts().sort_index()
        values2 = Severity2['Start_Time'].dt.year.value_counts().sort_index()
        values3 = Severity3['Start_Time'].dt.year.value_counts().sort_index()
        values4 = Severity4['Start_Time'].dt.year.value_counts().sort_index()


        trace1 = go.Bar(
            x=categories,
            y=values1.values,
            name='Series 1'
        )
        trace2 = go.Bar(
            x=categories,
            y=values2.values,
            name='Series 2'
        )
        trace3 = go.Bar(
            x=categories,
            y=values3.values,
            name='Series 3'
        )
        trace4 = go.Bar(
            x=categories,
            y=values4.values,
            name='Series 4'
        )

        # Create the figure
        fig = go.Figure(data=[trace1, trace2, trace3, trace4])

        # Update layout for better visualization
        fig.update_layout(
            title='Multiple Bar Chart',
            #xaxis=dict(title='Categories'),
            #yaxis=dict(title='Values'),
            barmode='group',  # This will group the bars side by side
            bargap=0.15,      # Gap between bars of adjacent location coordinates
            bargroupgap=0.1   # Gap between bars of the same location coordinate
        )

        return fig
    
    if (TimeInterval == 'Monthly'):
        categories = df['Start_Time'].dt.month.value_counts().sort_index().index

        values1 = Severity1['Start_Time'].dt.month.value_counts().sort_index()
        values2 = Severity2['Start_Time'].dt.month.value_counts().sort_index()
        values3 = Severity3['Start_Time'].dt.month.value_counts().sort_index()
        values4 = Severity4['Start_Time'].dt.year.value_counts().sort_index()

        trace1 = go.Bar(
            x=categories,
            y=values1.values,
            name='Series 1',
            
        )
        trace2 = go.Bar(
            x=categories,
            y=values2.values,
            name='Series 2',
            
        )
        trace3 = go.Bar(
            x=categories,
            y=values3.values,
            name='Series 3',
            
        )
        trace4 = go.Bar(
            x=categories,
            y=values4.values,
            name='Series 4',
            
        )

        # Create the figure
        fig = go.Figure(data=[trace1, trace2, trace3, trace4])
        # Update layout for better visualization
        fig.update_layout(
            title='Multiple Bar Chart',
            #xaxis=dict(title='Categories'),
            #yaxis=dict(title='Values'),
            barmode='group',  # This will group the bars side by side
            bargap=0.15,      # Gap between bars of adjacent location coordinates
            bargroupgap=0.1   # Gap between bars of the same location coordinate
        )

        return fig
    
    if (TimeInterval == 'Daily'):
        categories = df['Start_Time'].dt.dayofweek.value_counts().sort_index().index

        values1 = Severity1['Start_Time'].dt.dayofweek.value_counts().sort_index()
        values2 = Severity2['Start_Time'].dt.dayofweek.value_counts().sort_index()
        values3 = Severity3['Start_Time'].dt.dayofweek.value_counts().sort_index()
        values4 = Severity4['Start_Time'].dt.year.value_counts().sort_index()

        trace1 = go.Bar(
            x=categories,
            y=values1.values,
            name='Series 1'
        )
        trace2 = go.Bar(
            x=categories,
            y=values2.values,
            name='Series 2'
        )
        trace3 = go.Bar(
            x=categories,
            y=values3.values,
            name='Series 3'
        )

        trace4 = go.Bar(
            x=categories,
            y=values4.values,
            name='Series 4'
        )

        # Create the figure
        fig = go.Figure(data=[trace1, trace2, trace3, trace4])
        # Update layout for better visualization
        fig.update_layout(
            title='Multiple Bar Chart',
            #xaxis=dict(title='Categories'),
            #yaxis=dict(title='Values'),
            barmode='group',  # This will group the bars side by side
            bargap=0.15,      # Gap between bars of adjacent location coordinates
            bargroupgap=0.1   # Gap between bars of the same location coordinate
        )

        return fig
    
    if (TimeInterval == 'Hourly'):
        categories = df['Start_Time'].dt.hour.value_counts().sort_index().index

        values1 = Severity1['Start_Time'].dt.hour.value_counts().sort_index()
        values2 = Severity2['Start_Time'].dt.hour.value_counts().sort_index()
        values3 = Severity3['Start_Time'].dt.hour.value_counts().sort_index()
        values4 = Severity4['Start_Time'].dt.year.value_counts().sort_index()

        trace1 = go.Bar(
            x=categories,
            y=values1.values,
            name='Series 1'
        )
        trace2 = go.Bar(
            x=categories,
            y=values2.values,
            name='Series 2'
        )
        trace3 = go.Bar(
            x=categories,
            y=values3.values,
            name='Series 3'
        )
        trace4 = go.Bar(
            x=categories,
            y=values4.values,
            name='Series 4'
        )

        # Create the figure
        fig = go.Figure(data=[trace1, trace2, trace3, trace4])
        # Update layout for better visualization
        fig.update_layout(
            title='Multiple Bar Chart',
            #xaxis=dict(title='Categories'),
            #yaxis=dict(title='Values'),
            barmode='group',  # This will group the bars side by side
            bargap=0.15,      # Gap between bars of adjacent location coordinates
            bargroupgap=0.1   # Gap between bars of the same location coordinate
        )

        return fig

MultiBarChart(df_acc,'Monthly').show()

### Second graph (Piechart):
Severity distribution (Little consequence, Medium consequence, High consequence, Very High consequences)

In [10]:
#pie chart for distribution of severity of the accident
def PieChart(df):
    # Calculate the distribution of 'severity'
    severity_counts = df['Severity'].value_counts().sort_index()

    # Create a pie chart
    fig = px.pie(values=severity_counts, names=severity_counts.index, title="Distribution of Severity")

    return fig

# Display the pie chart
PieChart(df_acc).show()

In [68]:
def BestWorstBarChart(df_acc, df_pop, year, best):
    
    state_to_index = {
        'AL': 0,
        'AK': 1,
        'AZ': 2,
        'AR': 3,
        'CA': 4,
        'CO': 5,
        'CT': 6,
        'DE': 7,
        'FL': 8,
        'GA': 9,
        'HI': 10,
        'ID': 11,
        'IL': 12,
        'IN': 13,
        'IA': 14,
        'KS': 15,
        'KY': 16,
        'LA': 17,
        'ME': 18,
        'MD': 19,
        'MA': 20,
        'MI': 21,
        'MN': 22,
        'MS': 23,
        'MO': 24,
        'MT': 25,
        'NE': 26,
        'NV': 27,
        'NH': 28,
        'NJ': 29,
        'NM': 30,
        'NY': 31,
        'NC': 32,
        'ND': 33,
        'OH': 34,
        'OK': 35,
        'OR': 36,
        'PA': 37,
        'RI': 38,
        'SC': 39,
        'SD': 40,
        'TN': 41,
        'TX': 42,
        'UT': 43,
        'VT': 44,
        'VA': 45,
        'WA': 46,
        'WV': 47,
        'WI': 48,
        'WY': 49,
    }
    
    df = df_acc

    if(year != 'all'): 

        #filter only interest year
        df = df_acc[(df_acc['Start_Time'].dt.year == year)]

        #initialize vector storing accidents
        state_acc_count = [0] * len(state_to_index)

        # Iterate through the dataset and update the vector
        for i in range(len(df)):
            state = ((df.iloc[i])['State'])
            
            if (state in state_to_index):
                state_acc_count[state_to_index[state]] += 1

            # normalize accident vector
            
            population_row = df_pop[df_pop['Year']==year]
            population_row = population_row.drop(['Year'],axis=1)
            population_array = population_row.iloc[0].to_numpy()
            state_acc_count =  np.divide(state_acc_count, population_array)
            
            print('acc')
            print (population_array)
            
            print('pop')
            print(state_acc_count)
        #return population_array
    else:
        return 0

BestWorstBarChart(df_acc,df_pop,2016,True)

acc
[ 4860545   741522  6941072  2989918 39250017  5540545  3576452   952065
 20612439 10310371  1428557  1683140 12801539  6633053  3134693  2907289
  4436974  4681666  1331479  6016447  6811779  9928300  5519952  2988726
  6093000  1042520  1907116  2940058  1334795  8944469  2081015 19745289
 10146788   757952 11614373  3923561  4093465 12784227  1056426  4961119
   865454  6651194 27862596  3051217   624594  8411808  7288000  1831102
  5778708   585501]
pop
[0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.00358904 0.         0.         0.         0.         0.
 0.         0.        ]
acc
[ 4860545   741522  6941072  29899

In [11]:
def BestWorstBarChart(df_acc, df_pop, year, best):

    #states dictionary
    state_to_index = {
        'Alabama': 0,
        'Alaska': 1,
        'Arizona': 2,
        'Arkansas': 3,
        'California': 4,
        'Colorado': 5,
        'Connecticut': 6,
        'Delaware': 7,
        'Florida': 8,
        'Georgia': 9,
        'Hawaii': 10,
        'Idaho': 11,
        'Illinois': 12,
        'Indiana': 13,
        'Iowa': 14,
        'Kansas': 15,
        'Kentucky': 16,
        'Louisiana': 17,
        'Maine': 18,
        'Maryland': 19,
        'Massachusetts': 20,
        'Michigan': 21,
        'Minnesota': 22,
        'Mississippi': 23,
        'Missouri': 24,
        'Montana': 25,
        'Nebraska': 26,
        'Nevada': 27,
        'New Hampshire': 28,
        'New Jersey': 29,
        'New Mexico': 30,
        'New York': 31,
        'North Carolina': 32,
        'North Dakota': 33,
        'Ohio': 34,
        'Oklahoma': 35,
        'Oregon': 36,
        'Pennsylvania': 37,
        'Rhode Island': 38,
        'South Carolina': 39,
        'South Dakota': 40,
        'Tennessee': 41,
        'Texas': 42,
        'Utah': 43,
        'Vermont': 44,
        'Virginia': 45,
        'Washington': 46,
        'West Virginia': 47,
        'Wisconsin': 48,
        'Wyoming': 49,
    }

    df = df_acc
    if(year != 'all'): #filter only interest year
        
        df = df_acc[(df_acc['Start_Time'].dt.year == year)]

        #initialize vector storing accidents
        state_acc_count = [0] * len(state_to_index)



        # Initialize a vector accident per capita
        state_acc_ppl = [0] * len(state_to_index)

        # Iterate through the dataset and update the vector
        for state in df:
            if state in state_to_index:
                index = state_to_index[state]
                state_acc_count[index] += 1

        # Get the index of the year in the dataset
        #header = "State,2016,2017,2018,2019,2020,2021,2022"
        #year_index = header.split(',').index(str(year))

        # Iterate through the dataset and update the population vector
        #for row in df_pop:
        #    data = row.split(',')

        # Initialize a vector storing population
        population_vector = df_pop[df_pop['State']==year]
            
        print (df_pop)

            #state = data[0]
            #if state in state_to_index:
            #    index = state_to_index[state]
            #    population_vector[index] = int(data[year_index])
    
        # normalize accident vector
        #state_acc_count =  np.divide(state_acc_count, population_vector)
            
            
        #return year_index
    print(population_vector = df_pop[df_pop['State']==year])

BestWorstBarChart(df_acc,df_pop,2016,True)
print(df_pop[(df_pop['Year']==2019)])


KeyError: 'State'

In [ ]:
# number of accidents per year

# Create a bar chart
#fig = px.bar(

#            df, 
             #yearly
#             x=year_counts.index, 
#             y=year_counts.values,          
             
#             labels={'x': 'Year', 'y': 'Number of Accidents'},
#             title='Number of Accidents per Year')


# Show the figure
#fig.show()

In [ ]:
# number of accidents by month

# Create a bar chart

#fig = px.bar(

#            df, 
             #monthly
             #x=Month_counts.index, 
             #y=Month_counts.values,          
             
             #labels={'x': 'Month', 'y': 'Number of Accidents'},
             #title='Number of Accidents per Month')


# Show the figure
#fig.show()

In [ ]:
# number of accidents by Day of the week

# Create a bar chart
#fig = px.bar(
#            df, 
            
             #daylyofweek
#             x=Dayly_counts.index, 
#             y=Dayly_counts.values,
            
#             labels={'x': 'Day of the week', 'y': 'Number of Accidents'},
#             title='Number of Accidents per Day of the Week')


# Show the figure
#fig.show()

In [ ]:
# number of accidents by Hour of the day

# Create a bar chart
#fig = px.bar(
#            df, 
            
             #daylyofweek
#             x=Howrly_counts.index, 
#             y=Howrly_counts.values,
            
#             labels={'x': 'Hour', 'y': 'Number of Accidents'},
#             title='Number of Accidents per Hour of the dayk',
#)

# Show the figure
#fig.show()